In [ ]:
#Folium Test Program
# To install folium to your computer run the following:
# conda install --channel https://conda.anaconda.org/conda-forge folium
# We will also want to install shapely to do a bit of geocoding, so to install this run:
# conda install shapely


In [47]:
import folium
import pandas as pd
import numpy as np
from datetime import datetime
import urllib
import json

In [48]:
map_osm = folium.Map(location=[37.79086, -122.40147], zoom_start=14)
folium.Marker([37.79086, -122.40147], popup='General Assembly'
              ).add_to(map_osm)
map_osm

In [58]:
def read_geo_url(url):
    in_file = urllib.urlopen(url)
    return json.load(in_file)

In [50]:
state_url = 'https://raw.githubusercontent.com/python-visualization/folium/master/examples/us-states.json'
state_geo = read_geo_url(state_url)
state_unemployment = (
    r'https://raw.githubusercontent.com/python-visualization/folium/master/examples/US_Unemployment_Oct2012.csv')

state_data = pd.read_csv(state_unemployment)

state_data.head()

# To view json go to the following link:
# https://raw.githubusercontent.com/python-visualization/folium/master/examples/us-states.json

State  Unemployment
0    AL           7.1
1    AK           6.8
2    AZ           8.1
3    AR           7.2
4    CA          10.1

In [51]:
#Let Folium determine the scale and view Choropleth
states = folium.Map(location=[40, -102], zoom_start=4)
states.choropleth(geo_str=state_str, data=state_data,
                columns=['State', 'Unemployment'],
                key_on='feature.id',
                fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Unemployment Rate (%)')
states
# To load a choropleth map from your hard drive use geo_path (i.e.)
#states.choropleth(geo_path='states.geojson', data=state_data,
#                columns=['State', 'Unemployment'], 
#                key_on='feature.id',
#                fill_color='YlGn', fill_opacity=0.7, line_opacity=0.2,
#                legend_name='Unemployment Rate (%)')

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


Lets start with a more local version 

A topic near and dear to my heart, 
human feces in San Francisco

View this map published by the amazing William Mees. https://willyem.carto.com/viz/156b1e0c-5b45-11e5-9351-0e018d66dc29/public_map

http://www.citylab.com/housing/2015/10/mapping-san-franciscos-sidewalk-pooping-problem/409561/

My plan for this exercise is to import 
in the GeoJson file for human feces over the last few years 
in San Francisco, as a way to visualize how the data is spread out over the years.

I will also be using a San Francisco geojson map of neighborhoods, and combining this with a dataset of excrement sightings to visualize it as an aggregate of data per neighborhood.

I will first just show a simple map of the points shown in the data set that William gathered. 

In [59]:
poop_url = r"https://raw.githubusercontent.com/joshuacano/DS-SF-24/master/folium_lecture/2009_poop.json"
poop_data = read_geo_url(poop_url)

In [60]:
# Let's look at the first poop instance!
poop_data['features'][0]

{u'geometry': {u'coordinates': [-122.420202, 37.789322], u'type': u'Point'},
 u'properties': {u'address': u'1338 POLK ST, SAN FRANCISCO, CA, 94109',
  u'cartodb_id': 48355,
  u'caseid': 347563,
  u'category': u'Street and Sidewalk Cleaning',
  u'closed': u'01/29/2009 09:09:47 AM',
  u'field_1': 48354,
  u'lat': 37.789322012,
  u'lon': -122.420202321,
  u'neighborhood': u'Nob Hill',
  u'opened': u'2009-01-08T17:04:22Z',
  u'point': u'(37.789322012, -122.420202321)',
  u'request_details': u'Human_waste_or_urine',
  u'request_type': u'Sidewalk_Cleaning',
  u'responsible_agency': u'DPW Ops Queue',
  u'source': u'Voice In',
  u'status': u'Closed',
  u'supervisor_district': 3,
  u'updated': u'01/29/2009 09:09:47 AM'},
 u'type': u'Feature'}

In [56]:
geo_path = "https://raw.githubusercontent.com/joshuacano/DS-SF-24/master/folium_lecture/2009_poop.json"
in_file = urllib.urlopen(geo_path)
geo_str = json.load(in_file)
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_str=geo_str)
poop_map

In [63]:
#Lets overlay that with some neighborhood break downs.
# I took this data from code america. Thanks Code America!
# https://github.com/codeforamerica/click_that_hood/blob/master/public/data/san-francisco.geojson

sf_path='https://raw.githubusercontent.com/joshuacano/DS-SF-24/master/folium_lecture/san-francisco.geojson'
hood_json = read_geo_url(sf_path)

#Add style attributes
my_style = {
    "color": "#ff7800",
    "weight": 2,
    "opacity": 0.65
}
folium.GeoJson(hood_json,
               style_function=lambda x: my_style, overlay=True).add_to(poop_map)

poop_map

Okay, so this looks a little bit funky. But its got some good information on it, 
so lets try and aggregate all this data together using pandas!

First, lets read our data into a dataframe and get the details we need from it

In [65]:
# Seems like we will want the point, the date it was opened, the casid, 
# the neighborhood, and the supervisor_district, that could be interesting!
def get_details(item):
    details = {}
    details['point'] = item['geometry']['coordinates']
    details['date_opened'] = item['properties']['opened']
    details['caseid'] = item['properties']['caseid']
    details['neighborhood'] = item['properties']['neighborhood']
    details['supervisor_district'] = item['properties']['supervisor_district']
    return details

rs = []
for incident in poop_data['features']:
    rs.append(get_details(incident))
poop_frame = pd.DataFrame(rs)
print len(poop_frame)
poop_frame.head()

429


caseid           date_opened           neighborhood  \
0  347563  2009-01-08T17:04:22Z               Nob Hill   
1  344432  2009-01-04T18:34:14Z               Nob Hill   
2  346191  2009-01-06T23:18:01Z                Mission   
3  363446  2009-01-31T18:30:28Z               Nob Hill   
4  363402  2009-01-31T17:38:40Z  Downtown/Civic Center   

                      point  supervisor_district  
0  [-122.420202, 37.789322]                    3  
1  [-122.420824, 37.789924]                    3  
2  [-122.420174, 37.757312]                    9  
3  [-122.421282, 37.791854]                    3  
4  [-122.419573, 37.785969]                    6

In [66]:
poop_frame.groupby(['neighborhood']).count()

caseid  date_opened  point  supervisor_district
neighborhood                                                          
Bayview                     6            6      6                    6
Bernal Heights              2            2      2                    2
Castro/Upper Market         7            7      7                    7
Chinatown                   4            4      4                    4
Downtown/Civic Center     153          153    153                  153
Excelsior                  15           15     15                   15
Financial District          7            7      7                    7
Glen Park                   1            1      1                    1
Haight Ashbury              3            3      3                    3
Inner Richmond              4            4      4                    4
Inner Sunset                2            2      2                    2
Marina                      4            4      4                    4
Mission                    48           48     48                   48
Nob Hill                   30           30     30                   30
Noe Valley                  2            2      2                    2
North Beach                 8            8      8                    8
Outer Mission               7            7      7                    7
Outer Richmond              2            2      2                    2
Outer Sunset                8            8      8                    8
Parkside                    2            2      2                    2
Potrero Hill                2            2      2                    2
Presidio Heights            2            2      2                    2
Russian Hill                6            6      6                    6
South of Market            68           68     68                   68
Visitacion Valley           3            3      3                    3
West of Twin Peaks          8            8      8                    8
Western Addition           25           25     25                   25

In [68]:
# K so it seems like we have a much bigger amount of neighborhoods in the incident data,
# than in our neighborhood layer. 
# lets try and match each incident to the existing neighborhood layer we got.
# For that we will use the shapely library we just downloaded.
import shapely.geometry
point = shapely.geometry.Point (poop_frame.point[0])

In [69]:
print datetime.now()
hood_shapes = []

for feature in hood_json["features"]:
    hood_shapes.append({
            "shape" : shapely.geometry.shape(feature["geometry"]),
             "name" : feature['properties']['name']})
    

poop_frame['shape_neighborhood'] = None
for hood_shape in hood_shapes:
    for row in poop_frame.loc[poop_frame['shape_neighborhood'].isnull(),:].itertuples():
        point = shapely.geometry.Point(row.point)
        # This will check to see if the incident was in the neighborhood
        if hood_shape['shape'].contains(point):
            poop_frame.loc[row[0], 'shape_neighborhood'] = hood_shape['name']
print datetime.now()

2016-08-02 21:28:53.826532
2016-08-02 21:28:55.173646


In [73]:
# Ok so now that we know how to match an incident with our existing neighborhood geojson file,
# lets make a new dataframe that has all the neighborhoods with their frequency per neighborhood 
freq_frame = poop_frame.groupby(['shape_neighborhood']).count()
freq_frame['shape_neighborhood'] = freq_frame.index

In [74]:
# Now lets associate it with our original neighborhood map.
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_str=hood_json,
                    data=freq_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')
poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:8: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [82]:
# We can see the automated legend is thrown off by the outliers, lets send in our own legend
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_str=hood_json,
                    data=freq_frame,
                columns=['shape_neighborhood', 'caseid'],
                threshold_scale=[5,20,40,60,80, 400],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

In [279]:
def get_year(start_date, end_date, frame):
    df = frame.groupby(['shape_neighborhood']).count()
    df.caseid = 0
    date_frame = frame[(frame.date_opened >= start_date) &
                       (frame.date_opened < end_date)]
    date_frame = date_frame.groupby(['shape_neighborhood']).count()['caseid']
    df.update(date_frame)
    df.caseid = df.caseid.astype(int)
    df['shape_neighborhood'] = df.index
    return df

In [280]:
# Lets try on a per year basis!
year_view = get_year('2009-01-01', '2010-01-01', poop_frame)
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
sf_counties = 'visualization_lecture/san-francisco.geojson'
poop_map.choropleth(geo_path=sf_counties,
                    data=year_view,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:13: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [207]:
#2010
date_frame = get_year("2008-01-01", "2009-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:19: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [208]:
date_frame = get_year("2010-01-01", "2011-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [210]:
date_frame = get_year("2011-01-01", "2012-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [211]:
date_frame = get_year("2012-01-01", "2013-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map

/anaconda/lib/python2.7/site-packages/ipykernel/__main__.py:9: FutureWarning: 'threshold_scale' default behavior has changed. Now you get a linear scale between the 'min' and the 'max' of your data. To get former behavior, use folium.utilities.split_six.


In [258]:
def get_threshold_scale(frame, column):
    """Get Threshold scale for frame
    
    We will use a larger than normal range for the first 4 scales.
    In order to get some more separation for the tiles"""
    rs = []
    for i in np.linspace(0.01, 0.9, 6, endpoint=True):
        rs.append(frame[frame[column] >0][column].quantile(i))
    return rs


date_frame = get_year("2013-01-01", "2014-01-01", poop_frame)
date_frame['shape_neighborhood'] = date_frame.index
poop_map = folium.Map(location=[37.79086, -122.40147], zoom_start=12)
poop_map.choropleth(geo_path=sf_counties,
                    data=date_frame,
                columns=['shape_neighborhood', 'caseid'],
                threshold_scale=(get_threshold_scale(date_frame, 'caseid')),
                key_on='feature.properties.name',
                fill_color='YlOrRd', fill_opacity=0.7, line_opacity=0.2,
                legend_name='Poop Frequency')

poop_map